# Setup

In [1]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


set working directory to guitarist-net and add to path

In [2]:
# %cd /content/drive/Othercomputers/My MacBook Pro/guitarist-net
%cd /content/drive/MyDrive/Research/guitarist-net

/content/drive/.shortcut-targets-by-id/1-6NpHp6YPF3lnflUjDexvjkAXIGBOlME/guitarist-net


install requirements

In [3]:
!pip install -r requirements.txt &> /dev/null

imports

In [4]:
import numpy as np
import torch
import torch.nn as nn
import matplotlib.pyplot as plt
from plot_listen.listen import play
from plot_listen.plot import plot
from util import count_params
from globals import *
from data.gset_midi_dataset import GsetMidiDataset
from midi_synth.midi_synth import MidiSynth
from train.model_trainer import ModelTrainer

# Set up Training

get datasets

In [5]:
# train_dataset = GsetMidiDataset(name="train_player-not00_gset-midi_1.0s.npz")
train_dataset = GsetMidiDataset()

Type a number to select an option:
	0)	test_player-00_gset-midi_1.0s.npz
	1)	train_player-not00_gset-midi_1.0s.npz
	2)	test_player-00_gset-midi_3.0s.npz
	3)	train_player-not00_gset-midi_3.0s.npz
	4)	test_player-00_solo_gset-midi_1.0s.npz
	5)	train_player-not00_solo_gset-midi_1.0s.npz
	6)	train_player-05_fingerstyle_gset-midi_3.0s.npz
	7)	valid_player-00_fingerstyle_gset-midi_3.0s.npz
	8)	test_players-0304_fingerstyle_gset-midi_3.0s.npz
Selection: 6
train_player-05_fingerstyle_gset-midi_3.0s.npz


In [6]:
# test_dataset = GsetMidiDataset(name="test_player-00_gset-midi_1.0s.npz")
test_dataset = GsetMidiDataset()

Type a number to select an option:
	0)	test_player-00_gset-midi_1.0s.npz
	1)	train_player-not00_gset-midi_1.0s.npz
	2)	test_player-00_gset-midi_3.0s.npz
	3)	train_player-not00_gset-midi_3.0s.npz
	4)	test_player-00_solo_gset-midi_1.0s.npz
	5)	train_player-not00_solo_gset-midi_1.0s.npz
	6)	train_player-05_fingerstyle_gset-midi_3.0s.npz
	7)	valid_player-00_fingerstyle_gset-midi_3.0s.npz
	8)	test_players-0304_fingerstyle_gset-midi_3.0s.npz
Selection: 7
valid_player-00_fingerstyle_gset-midi_3.0s.npz


create model

In [7]:
synth = MidiSynth()

In [8]:
print(synth)
count_params(synth)

MidiSynth(
  (context_network): ContextNetwork(
    (linear1): Linear(in_features=12, out_features=32, bias=True)
    (leakyReLU): LeakyReLU(negative_slope=0.01)
    (gru): GRU(32, 64, batch_first=True)
    (layer_norm): LayerNorm((64,), eps=1e-05, elementwise_affine=True)
    (linear2): Linear(in_features=64, out_features=32, bias=True)
  )
  (mono_network): MonoNetworkSmall(
    (string_emb_layer): Embedding(6, 6)
    (linear1): Linear(in_features=40, out_features=128, bias=True)
    (leakyReLU1): LeakyReLU(negative_slope=0.01)
    (gru): GRU(128, 192, batch_first=True)
    (linear2): Linear(in_features=192, out_features=128, bias=True)
    (leakyReLU2): LeakyReLU(negative_slope=0.01)
    (layer_norm): LayerNorm((128,), eps=1e-05, elementwise_affine=True)
    (dense_amplitudes): Linear(in_features=128, out_features=102, bias=True)
    (dense_filter_coeffs): Linear(in_features=128, out_features=65, bias=True)
  )
  (harmonic_oscillator): HarmonicOscillator(
    (upsample): Upsample(sc

(274701, {'context_network': 21440, 'mono_network': 237259, 'reverb': 16002})

## Optionally Freeze/Unfreeze Params

In [9]:
# modules_to_freeze = ("context_network","mono_network") 

In [10]:
# for name, param in synth.named_parameters():
#     module_name = name.split(".")[0]
#     if module_name in modules_to_freeze:
#         param.requires_grad = False
#     else:
#         param.requires_grad = True
    


In [11]:
# count_params(synth)

## create trainer

In [12]:
trainer = ModelTrainer(synth, train_dataset, test_dataset)

load checkpoint

In [13]:
trainer.load_checkpoint(load_latest=True)

Type a number to select an option:
	0)	2022-11-15 07:09PM MIDI Synth : train midi synth
	1)	2022-11-18 11:24AM MIDI Synth : reduced model capacity
	2)	2022-11-18 05:05PM MIDI Synth : midi synth with sc osc and noise
	3)	2022-11-18 06:44PM MIDI Synth : train with mfcc input
	4)	2022-11-19 01:17PM MIDI Synth : mfcc with slightly larger model
	5)	2022-11-29 05:03PM MIDI Synth : no string emb
	6)	2022-11-30 07:46PM MIDI Synth : pitch adjustment
	7)	2022-12-08 01:44PM MIDI Synth : lr=0.0001
	8)	2023-02-17 10:56AM MIDI Synth : spectral loss alpha = 2
	9)	2023-02-17 11:39AM MIDI Synth : spectral loss alpha = 1_5
	10)	2023-03-23 07:57PM MIDI Synth : alpha=8.0
	11)	2023-03-24 10:44AM MIDI Synth : resume prev with now working F0
	12)	2023-03-24 11:53AM MIDI Synth : working f0, alpha=8.0
	13)	2023-03-24 01:03PM MIDI Synth : resume prev
	14)	2023-03-27 02:36PM MIDI Synth : alpha1
	15)	2023-03-27 07:57PM MIDI Synth : test context
	16)	2023-03-28 11:44AM MIDI Synth : overfit-batch4_lr-3e4
	17)	2023-

# Training

train model

In [ ]:
trainer.train_model(consolidate_output=True)

  0%|          | 0/21 [00:00<?, ?it/s]

  0%|          | 0/21 [00:00<?, ?it/s]

ERROR:root:Internal Python error in the inspect module.
Below is the traceback from this internal error.

ERROR:root:Internal Python error in the inspect module.
Below is the traceback from this internal error.

ERROR:root:Internal Python error in the inspect module.
Below is the traceback from this internal error.



Traceback (most recent call last):
  File "/usr/local/lib/python3.9/dist-packages/IPython/core/interactiveshell.py", line 3553, in run_code
    exec(code_obj, self.user_global_ns, self.user_ns)
  File "<ipython-input-14-b98c4b58ce6c>", line 1, in <cell line: 1>
    trainer.train_model(consolidate_output=True)
  File "/content/drive/.shortcut-targets-by-id/1-6NpHp6YPF3lnflUjDexvjkAXIGBOlME/guitarist-net/train/model_trainer.py", line 329, in train_model
  File "/content/drive/.shortcut-targets-by-id/1-6NpHp6YPF3lnflUjDexvjkAXIGBOlME/guitarist-net/train/model_trainer.py", line 278, in valid_epoch
  File "/usr/local/lib/python3.9/dist-packages/torch/nn/modules/module.py", line 1501, in _call_impl
    return forward_call(*args, **kwargs)
  File "/content/drive/.shortcut-targets-by-id/1-6NpHp6YPF3lnflUjDexvjkAXIGBOlME/guitarist-net/midi_synth/midi_synth.py", line 199, in forward
  File "/content/drive/.shortcut-targets-by-id/1-6NpHp6YPF3lnflUjDexvjkAXIGBOlME/guitarist-net/midi_synth/midi_syn